![](ubc_header.png)

# Climate-Friendly Food Systems (CFFS) Labelling Project

### The University of British Columbia

****

## Part I: Data Preprocessing

## Set up and Import Libraries

In [1]:
#pip install -r requirements.txt

In [2]:
import numpy as np
import pandas as pd
# import pdpipe as pdp
import matplotlib.pyplot as plt
import glob
import os
import csv
from itertools import islice
from decimal import Decimal
import xml.etree.ElementTree as et
from xml.etree.ElementTree import parse
import openpyxl
import pytest

In [1]:
# Changed the path here, May 2nd 2023
# Set the root path, change the the current working directory into the project folder
path = "C:/Users/ENTER_HERE/CFFS-S23/CFFS-22-23"
# path = os.getcwd()

# os.chdir is used to change the current directory to the specified path
os.chdir(path)
print(path)

In [4]:
# Enable reading data table in the scrolling window if you prefer
pd.set_option("display.max_rows", None, "display.max_columns", None)

****

## Load Data Files

### Set Data File Path

In [2]:
# Select data file path for the chosen venue and time range where the recipes data stored

# OK 2023

# filepath_list = glob.glob(os.path.join(os.getcwd(), "data", "raw", "OK 23-24 Sep-Dec*", "*.oc"))


# Totem 2023
filepath_list = glob.glob(os.path.join(os.getcwd(), "data", "raw", "Totem 23-24 Sep-Dec*", "*.oc"))

# Gather 2023
# filepath_list = glob.glob(os.path.join(os.getcwd(), "data", "raw", "Gather 23-24 Sep-Dec*", "*.oc"))


filepath_list

### Import Items List

In [6]:
# Read items.xml files in the filepath_list and construct a dataframe
ItemId = []
Description = []
CaseQty = []
CaseUOM = []
PakQty = []
PakUOM = []
InventoryGroup = []


# from the items xml file, findtext of CaseQty, CaseUOM, PakQty, PakUOM, and InventoryGroup
# then append it on the lists above

for filepath in filepath_list:
    path = filepath + '/items.xml'
    if os.path.isfile(path):
        xtree = et.parse(path)
        xroot = xtree.getroot()
        for item in xtree.iterfind('Item'):
            ItemId.append(item.attrib['id'])
            Description.append(item.findtext('Description'))
            CaseQty.append(item.findtext('CaseQty'))
            CaseUOM.append(item.findtext('CaseUOM'))
            PakQty.append(item.findtext('PakQty'))
            PakUOM.append(item.findtext('PakUOM'))
            InventoryGroup.append(item.findtext('InventoryGroup'))

            
# Create a dataframe from the lists created above.
        
Items = pd.DataFrame({'ItemId': ItemId, 'Description': Description, 'CaseQty': CaseQty, 
                      'CaseUOM': CaseUOM, 'PakQty': PakQty, 'PakUOM': PakUOM, 'InventoryGroup': InventoryGroup}
                    )
Items.drop_duplicates(inplace=True)

Items.reset_index(drop=True, inplace=True)

In [8]:
# creates a new array with unique ItemIds
all_id_list = Items["ItemId"].unique()

In [9]:
# None of the items are egg yolk liq
Items.loc[Items["Description"] == "Egg Yolk Liq"]

Empty DataFrame
Columns: [ItemId, Description, CaseQty, CaseUOM, PakQty, PakUOM, InventoryGroup]
Index: []

In [10]:
# Sumplemental option for egg, vegan option
Items.loc[Items["ItemId"] == "I-68700"]

ItemId                Description CaseQty CaseUOM PakQty PakUOM  \
504  I-68700  EGG CKD*FOLDED  VEGAN FRZ  60.000    each  1.000   each   

    InventoryGroup  
504          DAIRY

In [11]:
# Gives you the list of breads
breadlist = []
for ind, row in Items.iterrows():
    if ("LOAF" or "SANDWICH" "BREAD") in row["Description"]:
        breadlist.append(row["ItemId"])

breadlist

['I-47962',
 'I-13004',
 'I-33133',
 'I-13420',
 'I-47963',
 'I-1271',
 'I-1373',
 'I-11664',
 'I-15032',
 'I-71503',
 'I-12478']

In [12]:
# Based on info below there are 486 rows and 7 columns
Items.shape

(1618, 7)

In [13]:
Items.dtypes

ItemId            object
Description       object
CaseQty           object
CaseUOM           object
PakQty            object
PakUOM            object
InventoryGroup    object
dtype: object

In [14]:
# Save the dataframe to csv
path = os.path.join(os.getcwd(), "data", "preprocessed", "Items_List.csv")
Items.to_csv(path, index = False, header = True)

### Import Ingredients List

In [15]:
# Read ingredients.xml files in the filepath_list and construct a dataframe
IngredientId = []
Conversion = []
InvFactor = []
Qty = []
Recipe = []
Uom = []

# Using the Ingredients XML file, we extract attributes containing ingredients, conversion, invFactor, qty, recipe, and uom. 
# Then we append it onto the IngredientId, Coversion, InvFactor, Qty, Recipe, and Uom lists
# Then we create a dataframe using the lists created. 

for filepath in filepath_list:
    path = filepath + '/Ingredients.xml'
    if os.path.isfile(path):
        xtree = et.parse(path)
        xroot = xtree.getroot()
        for x in xtree.iterfind('Ingredient'):
            IngredientId.append(x.attrib['ingredient'])
            Conversion.append(x.attrib['conversion'])
            InvFactor.append(x.attrib['invFactor'])
            Qty.append(x.attrib['qty'])
            Recipe.append(x.attrib['recipe'])
            Uom.append(x.attrib['uom'])
    
Ingredients = pd.DataFrame({'IngredientId': IngredientId, 'Qty': Qty,'Uom': Uom, 'Conversion': Conversion, 
                      'InvFactor': InvFactor,'Recipe': Recipe}).drop_duplicates()
Ingredients.drop_duplicates(subset=["IngredientId", "Recipe"], inplace=True)

Ingredients.reset_index(drop=True, inplace=True)

In [16]:
Ingredients

IngredientId       Qty     Uom     Conversion  InvFactor   Recipe
0          P-48933     1.000      Kg     1.00000000     1.0000  P-10113
1           I-4626    16.000      CT     1.00000000     2.6667  P-10115
2          P-18746     1.000      Kg     1.00000000     1.0000  P-10241
3           I-3388     1.000       L     1.00000000     0.3058  P-10496
4           I-4658     2.270      Kg     2.20462000     0.6942  P-10496
5           I-1813    30.000      ml     0.03381406     9.6774  P-10502
6           I-3348     3.000       L     1.00000000     0.9677  P-10502
7          P-26020   100.000       g     0.00100000    32.2581  P-10502
8          P-45879     5.700      Kg     1.00000000     1.1111  P-10873
9           I-1821     1.000       L  1000.00000000     0.0286  P-10874
10          I-3458     2.840       L     1.00000000     0.0811  P-10874
11          I-3511     5.680       L     1.00000000     0.1623  P-10874
12          I-3698     1.000       L     1.00000000     0.0286  P-10874
13          I-4657   250.000       g     0.00220462     7.1429  P-10874
14          I-4658   250.000       g     0.00220462     7.1429  P-10874
15          I-5983    12.000       L     1.00000000     0.3429  P-10874
16          I-6028   300.000       g     0.00100000     8.5714  P-10874
17          I-6820   450.000       g     0.00100000    12.8571  P-10874
18         P-18746     2.500      Kg     1.00000000     0.0714  P-10874
19         P-41094     2.500      Kg     1.00000000     0.0714  P-10874
20         P-41095     2.500      Kg     1.00000000     0.0714  P-10874
21         P-50552     6.000      Kg     2.20462000     0.1714  P-10874
22          I-3623     0.500    Tbsp     5.29999987     0.1250  P-11120
23          I-3660     2.000     cup     0.20000000     0.5000  P-11120
24          I-3691     4.000       L     1.00000000     1.0000  P-11120
25          I-6026   120.000       g     1.00000000    30.0000  P-11120
26         I-11312     3.000       g     0.03527399     0.2727  P-11375
27          I-3225     5.640       L     1.00000000     0.5127  P-11375
28          I-3245   200.000       g     1.00000000    18.1818  P-11375
29          I-3501    20.000       g     0.00100000     1.8182  P-11375
30          I-3642    10.000       g     1.00000000     0.9091  P-11375
31          I-4620     2.000      CT     1.00000000     0.1818  P-11375
32          I-4742     2.250      Kg     2.20462000     0.2045  P-11375
33         I-47774   125.000      ml     0.00100000    11.3636  P-11375
34          I-4918    30.000       g     0.00220462     2.7273  P-11375
35          I-5983     4.000       L     1.00000000     0.3636  P-11375
36          I-6028   250.000       g     0.00100000    22.7273  P-11375
37          I-6443   225.000      ml     0.03381406    20.4545  P-11375
38          I-6820   450.000       g     0.00100000    40.9091  P-11375
39         P-18226   125.000      ml     0.00100000    11.3636  P-11375
40         P-26626     0.500     cup     0.22720000     0.0455  P-11375
41         P-26627     0.500     cup     0.22720000     0.0455  P-11375
42         I-13327     0.750     pak     1.00000000     0.0125  P-12392
43          I-1559    15.000      ml     0.00100000     0.2500  P-12392
44          I-1561    15.000      ml     0.00100000     0.2500  P-12392
45          I-1564    15.000      ml     0.00100000     0.2500  P-12392
46          I-2205     3.000      ml     0.00100000     0.0500  P-12392
47          I-2217     3.000      ml     0.00100000     0.0500  P-12392
48          I-2501     0.250     pak     1.00000000     0.0042  P-12392
49          I-4598     1.000      CT     1.00000000     0.0013  P-12954
50          I-4949    10.000      lb     1.00000000     1.6667  P-13445
51          I-4371     8.000      oz     0.06250000     8.0000  P-13469
52          I-4538    20.000      oz     0.06250000    20.0000  P-13469
53          I-4564    18.000      oz     0.06250000    18.0000  P-13469
54          I-4594     0.500      CT     1.000

In [17]:
# .loc attribute is used to filter rows and columns in a DataFrame based on if IngredientId is equal to I-29389

# This information tells us whether or not multiple recipes are using the same ingredient or not. Here we can see that 
# there are 3 recipes that use the same ingredient
Ingredients.loc[Ingredients["IngredientId"] == "I-29389"]

IngredientId      Qty Uom  Conversion InvFactor   Recipe
3333       I-29389    3.000  Kg  1.00000000    1.2000  P-50739
5361       I-29389  600.000   g  0.00100000  150.0000  P-56714
5753       I-29389  600.000   g  0.00100000  150.0000  P-57344
10819      I-29389   15.000   g  0.00100000    1.0000  R-56967

In [19]:
# This will output the IngredientId on the right side and the number of times the ingredient appears in the Ingredients
# dataframe on the left side. 

# The duplicated() method returns a Series with True and False values that describe which rows in the DataFrame are 
# duplicated and not.

check = Ingredients["IngredientId"].duplicated()

# The line below tells us at which index is the ingredient duplicated. For example I-4598 exists on index 2 of the dataframe and
# then again on index 8. So duplicate is first true on index 8, which is why it is printed below. It also appears in a below 
# index so it is printed again with that index number. 
Ingredients["IngredientId"][check]

14        I-4658
18       P-18746
35        I-5983
36        I-6028
38        I-6820
56        I-4626
71        I-3388
72        I-3642
73        I-6026
74        I-1813
77        I-3348
79        I-3388
91        I-5983
92        I-2156
95        I-3642
96        I-4766
98        I-2217
99        I-3284
100       I-3660
102       I-3388
105       I-4657
110       I-3388
125       I-3348
128      P-26020
138       I-5983
139       I-1813
140       I-3348
142      P-18907
146      I-13327
147       I-3388
148       I-3642
150       I-6026
151       I-3388
155       I-1813
158       I-4657
160      P-18907
162       I-6026
164       I-4538
166       I-4598
172       I-4626
180       I-5983
183       I-5983
186       I-5983
210       I-5983
211       I-4695
213       I-5983
215       I-5983
217       I-5983
219       I-5983
221       I-5983
223       I-5983
225       I-5983
227       I-5983
261      I-13327
262       I-5983
263       I-2501
264       I-5983
265       I-5983
268       I-59

In [20]:
# We can see from the printed items above that I-64877 does not appear because it does not get duplicated
Ingredients.loc[Ingredients["IngredientId"] == "I-64877"]

IngredientId    Qty Uom  Conversion InvFactor   Recipe
11770      I-64877  1.000  ea  1.00000000    1.0000  R-64999
12056      I-64877  2.000  ea  1.00000000    1.0000  R-67362
12605      I-64877  1.000  ea  1.00000000    1.0000  R-71576

In [23]:
Ingredients.loc[Ingredients["IngredientId"] == "I-64877"]

IngredientId    Qty Uom  Conversion InvFactor   Recipe
11770      I-64877  1.000  ea  1.00000000    1.0000  R-64999
12056      I-64877  2.000  ea  1.00000000    1.0000  R-67362
12605      I-64877  1.000  ea  1.00000000    1.0000  R-71576

In [24]:
# Below we are checking if we can extract an entire recipe. So we can do .loc with the particular recipe id and then 
# print all the data points (ingredientId, Qty, Uom, Conversion, InvFactor) for that recipe. 
Ingredients.loc[Ingredients["Recipe"] == "R-68698"]

Empty DataFrame
Columns: [IngredientId, Qty, Uom, Conversion, InvFactor, Recipe]
Index: []

In [25]:
Items.loc[Items["ItemId"] == "I-68700"]

ItemId                Description CaseQty CaseUOM PakQty PakUOM  \
504  I-68700  EGG CKD*FOLDED  VEGAN FRZ  60.000    each  1.000   each   

    InventoryGroup  
504          DAIRY

In [26]:
Ingredients.shape

(12675, 6)

In [27]:
Ingredients.dtypes

IngredientId    object
Qty             object
Uom             object
Conversion      object
InvFactor       object
Recipe          object
dtype: object

In [28]:
# Save the dataframe to csv
path = os.path.join(os.getcwd(), "data", "preprocessed", "Ingredients_List.csv")
Ingredients.to_csv(path, index = False, header = True)

### Import Preps List

In [29]:
# Read preps.xml files in the filepath_list and construct a dataframe
PrepId = []
Description = []
PakQty = []
PakUOM = []
InventoryGroup = []


# Here we do the same thing for the Preps XML file where we find the columns using attrib function and then append it onto
# the dataframe called Preps. 

for filepath in filepath_list:
    path = filepath + '/Preps.xml'
    if os.path.isfile(path):
        xtree = et.parse(path)
        xroot = xtree.getroot()
        for x in xtree.iterfind('Prep'):
            PrepId.append(x.attrib['id'])
            Description.append(x.findtext('Description'))
            PakQty.append(x.findtext('PakQty'))
            PakUOM.append(x.findtext('PakUOM'))
            InventoryGroup.append(x.findtext('InventoryGroup'))
    
Preps = pd.DataFrame({'PrepId': PrepId, 'Description': Description,
                  'PakQty': PakQty, 'PakUOM':PakUOM, 'InventoryGroup': InventoryGroup}).drop_duplicates()
preps_columns = Preps.columns
Preps.drop_duplicates(subset=["PrepId"], inplace=True)

Preps.reset_index(drop=True, inplace=True)

In [30]:
Preps

PrepId                     Description    PakQty PakUOM  \
0     P-44338  2K18 - Sumac & Garlic Potatoes    21.000     Kg   
1     P-43744         2K18 - Thai Larb (Pork)     6.500     Kg   
2     P-44639      ADDlSoutheast Braised Beef    35.000     Kg   
3     P-65630                AQlCreme Caramel     6.000    PTN   
4     P-65625          AQlCreme Caramel(Flan)     1.000      L   
5     P-65629        AQlCremeCaramel(Caramel)   100.000     ml   
6     P-65590                AQlMiso Marinade     1.340      L   
7     P-65591                  AQlSalmon Miso     1.000  piece   
8     P-65594                AQlTofu Marinade   223.000     ml   
9     P-67545            BAKED|4 Cheese Penne    12.000     Kg   
10    P-71855         BAKED|Basil puff pastry   300.000   each   
11    P-26184                     BAKED|Beans     9.000     Kg   
12    P-56706          BAKED|Fish Greek Style     1.000     Kg   
13    P-26965   BAKED|Jalapeno Ched Cornbread    15.000     Kg   
14    P-67674     BAKED|Loaded Sweet Potatoes     6.000   each   
15    P-54666     BAKED|Pasta|Chicken Alfredo     6.176     Kg   
16    P-54664       BAKED|Pasta|Chorizo Penne     7.360     Kg   
17    P-56502        BAKED|Pasta|Shrimp Pesto     6.750     Kg   
18    P-26318               BAKED|Puff Pastry    10.000     ea   
19    P-51235                  BAKED|Rockfish     4.500     Kg   
20    P-54572  BAKED|Rockfish Escovitch(Test)     4.500     Kg   
21    P-67284             BAKED|Russet Potato   100.000   each   
22    P-56372             BATCH| Carne Asada      1.000     Kg   
23    P-56399      BATCH| Cilantro lime Rice    730.000      g   
24    P-56826         BATCH| Crab cake|SLIDER   840.000      g   
25    P-41321          BATCH| Fish Batter 2.0     1.200      L   
26    P-56559            BATCH| Glazed Beans    453.593      g   
27    P-56406           BATCH| Herbed Quinoa      1.000     Kg   
28    P-56409  BATCH| Mushroom Pot Pie|FILL       9.500     Kg   
29    P-56433        BATCH| Shrimp Remoulade      1.600     Kg   
30    P-43206     BATCH| SMOOTHIE| Mango|16oz     4.000    PTN   
31    P-56373        BATCH| Street Corn|ELOTE     2.300     Kg   
32    P-56387    BATCH| Szechuan Green Beans    500.000      g   
33    P-67553            BATCH|3 Bean Flautas    60.000   each   
34    P-67544            BATCH|4 Cheese Sauce    16.500      L   
35    P-71170    BATCH|Achiote Chicken|COOKED    35.000     Kg   
36    P-56953                BATCH|Bannock AR    12.000   each   
37    P-53246   BATCH|Barley Lentil Pilaf|POP     6.000     Kg   
38    P-44751          BATCH|BBQ Hoisin Sauce     1.000      L   
39    P-47328               BATCH|BBQ salmon    140.000    PTN   
40    P-56621          BATCH|Beef Bourguignon     3.500     Kg   
41    P-71427         BATCH|Beef Sausage roll    60.000   each   
42    P-56828           BATCH|Beef Slider Mix     5.000     Kg   
43    P-60377      BATCH|Beyond Bread Pudding     2.250     Kg   
44    P-68129               BATCH|Beyond Hash     2.200     Kg   
45    P-61845      BATCH|Bircher Muesli|VEGAN     2.500     Kg   
46    P-56334     BATCH|Black Bean Hash|VEGAN     3.100     Kg   
47    P-67663         BATCH|Black Bean Hummus   550.000      g   
48    P-26682  BATCH|Black/White Sesame Seeds   907.186      g   
49    P-56479  BATCH|Blood Orange Preserve AR     2.000      L   
50    P-56430        BATCH|Blueberry Compote    375.000     ml   
51    P-56992              BATCH|Braised Kale     1.900     Kg   
52    P-67591     BATCH|Buffalo Chicken Thigh    20.000     Kg   
53    P-26847    BATCH|Butter Chicken (Thigh)    90.000     Kg   
54    P-44422       BATCH|Butter Chicken Base    50.000      L   
55    P-61876  BATCH|Buttermilk Fried Chicken     5.000     Kg   
56    P-56113    BATCH|Cabbage & Apple braise     5.500     Kg   
57    P-71425               BATCH|Calabacitas     2.500     Kg   
58    P-71458          BATCH|Camarones Diabla     1.000     Kg   
59    P-67599    BATCH|Cauli&Broccoli Gratain  

In [31]:
# This tells us that there are not any duplicates in the Preps dataframe. There is a different process|ingredient pair for 
# all the recipes. 
check = Preps["PrepId"].duplicated().any()
print(check)

False


In [32]:
# There are 546 rows and 5 columns
Preps.shape

(1514, 5)

In [33]:
# Here we see there is only one place P-50739 is used in the Preps
Preps.loc[Preps["PrepId"] == "P-50739"]

PrepId             Description PakQty PakUOM InventoryGroup
318  P-50739  COMPOTE|Apple Cinnamon  2.500      L           PREP

In [34]:
Preps.dtypes

PrepId            object
Description       object
PakQty            object
PakUOM            object
InventoryGroup    object
dtype: object

In [35]:
# Save the dataframe to csv
path = os.path.join(os.getcwd(), "data", "preprocessed", "Preps_List.csv")
Preps.to_csv(path, index = False, header = True)

### Import Products List

In [36]:
# Read products.xml files in the filepath_list and construct a dataframe
ProdId = []
Description = []
SalesGroup = []

# From the XML file for products append the id into ProdId, description into Description, and SalesGroup into SalesGroup list.
# Make a dataframe out of the 3 lists
# Then also drop the duplicates in the Products dataframe

for filepath in filepath_list:
    path = filepath + '/Products.xml'
    if os.path.isfile(path):
        xtree = et.parse(path)
        xroot = xtree.getroot()
        for x in xtree.iterfind('Prod'):
            ProdId.append(x.attrib['id'])
            Description.append(x.findtext('Description'))
            SalesGroup.append(x.findtext('SalesGroup'))
        
Products = pd.DataFrame({'ProdId': ProdId, 'Description': Description, 'SalesGroup': SalesGroup})
Products.drop_duplicates(inplace=True)

Products.reset_index(drop=True, inplace=True)

In [37]:
Products

ProdId                     Description                      SalesGroup
0     R-47209            5 spice powder|spice                  FT HOMESKILLET
1     R-55408                      ADD|Cheese                           FEAST
2     R-63588                    ADD|CHICKEN                     FT GRAB & GO
3     R-63593           ADD|Chicken Strip Dip                       FT SIDES 
4     R-65790              ADD|Chili|TAILGATE                        SPECIALS
5     R-22896                    ADD|Crackers                           FEAST
6     R-62187                   ADD|Fried Egg            FT STICKS AND SPOONS
7     R-56809                  ADD|Guacamole                        FT SIDES 
8     R-62363             ADD|Havarti|1 SLICE                           FEAST
9     R-56468                      ADD|Kimchi                         ADD ONS
10    R-62301           ADD|Perogy|SIDE (4pc)                       FT SIDES 
11    R-44853                 ADD|Poached Egg                           FEAST
12    R-61856                      ADD|Prawns                           FEAST
13    R-64375                      ADD|SHRIMP                           FEAST
14    R-65788            ADD|Tailgate cheddar                        SPECIALS
15    R-61659    ALF|Pasta|Cauliflower Cheese                   OK - AL FORNO
16    R-56505       ALF|Pasta|Chicken Alfredo                   OK - AL FORNO
17    R-51303         ALF|Pasta|Chorizo Penne                   OK - AL FORNO
18    R-65631            AQlCreme Caramel|PTN                           FEAST
19    R-65622    AQlDynamite Power Plant Bowl                           FEAST
20    R-65620      AQlMiso Glazed Salmon Bowl                           FEAST
21    R-64338                 ASSORTED DANISH                       FT BAKERY
22    R-65918     BAKE| GF VEGAN RASPBRY CHOC        FOOD - BAKERY & DESSERTS
23    R-52751                 BAKE|Bagel Asst                       FT BAKERY
24    R-64357              BAKE|BAKED PRETZEL                    FT GRAB & GO
25    R-19583             BAKE|Cake|Ponderosa                       FT BAKERY
26    R-52747               BAKE|Cinnamon Bun                       FT BAKERY
27    R-52742           BAKE|Croissant|Almond                       FT BAKERY
28    R-52743           BAKE|Croissant|Cheese                       FT BAKERY
29    R-52744        BAKE|Croissant|Chocolate                       FT BAKERY
30    R-34270       BAKE|Croissant|Multigrain                       FT BAKERY
31    R-52741            BAKE|Croissant|Plain                       FT BAKERY
32    R-52793  BAKE|Croissant|Spinach Pepper                        FT BAKERY
33    R-52750      BAKE|Danish|Almond Pear|MC                       FT BAKERY
34    R-52749        BAKE|Danish|Supreme Asst                       FT BAKERY
35    R-21282            BAKE|Loaf|Sweet Asst                       FT BAKERY
36    R-46225                BAKE|Muffin|Asst                       FT BAKERY
37    R-20398                 BAKE|Scone|Asst                       FT BAKERY
38    R-47788  BAKE|Scone|Cran & Blueberry|MC                       FT BAKERY
39    R-64236             BAKED LAYS ORIGINAL                    FT GRAB & GO
40    R-56911    BATCH|Chili Garlic Tofu|SIDE                           SIDES
41    R-56908    BATCH|Crispy Fried Tofu|side                         ADD ONS
42    R-56807        BATCH|Fire Roasted Salsa                           SIDES
43    R-57000   BATCH|Roasted Carrots AR|Side                           FEAST
44    R-56286                     Beef Donair                           FEAST
45    R-63589            BENTO PORK DUMPLINGS                    FT GRAB & GO
46    R-70967           BERKIPOPIMAINIHALIBUT                           FEAST
47    R-71200    BERKIPOPIVEGETARIANIMUSHTART                           FEAST
48    R-38748  BERRIES & QUINOA SALAD W/ OW S                    FT GRAB & GO
49    R-64760       BEV\SMARTWATER  1L ANTIOX                    FT BEVERAGES
50    R-64761     BEV\Water|S

In [38]:
# Here we can see that there is only one R-56966 in the products 
Products.loc[Products["ProdId"] == "R-56966"]

ProdId                    Description     SalesGroup
889  R-56966  GR|Oats|Steel Cut|Maple Apple  FT SWEETGREEN

In [39]:
Products.dtypes

ProdId         object
Description    object
SalesGroup     object
dtype: object

In [40]:
# Here we can see that there is only one R-68698 in the products 
Products.loc[Products["ProdId"] == "R-68698"]

Empty DataFrame
Columns: [ProdId, Description, SalesGroup]
Index: []

In [41]:
Products.shape

(1632, 3)

In [42]:
Products.dtypes

ProdId         object
Description    object
SalesGroup     object
dtype: object

In [43]:
# Save the dataframe to csv
path = os.path.join(os.getcwd(), "data", "preprocessed", "Products_List.csv")
Products.to_csv(path, index = False, header = True)

### Import Conversions List

In [44]:
# Read conventions.xml files in the filepath_list and construct a dataframe
ConversionId = []
Multiplier = []
ConvertFromQty = []
ConvertFromUom = []
ConvertToQty = []
ConvertToUom = []

# From the XML file for Conversions append the id into ConversionId, multiplier into Multiplier, ConvertFrom->qty into 
# ConvertFromQty,ConvertFrom->uom into ConvertFromUom, ConvertTo->qty into ConvertToQty and and ConvertTo->uom into the
# CovertToUom list. 
# Make a dataframe out of the 3 lists
# Then also drop the duplicates in the Products dataframe


for filepath in filepath_list:
    path = filepath + '/Conversions.xml'
    if os.path.isfile(path):
        xtree = et.parse(path)
        xroot = xtree.getroot()
        for x in xtree.iterfind('Conversion'):
            ConversionId.append(x.attrib['id'])
            Multiplier.append(x.attrib['multiplier'])
            ConvertFromQty.append(x.find('ConvertFrom').attrib['qty'])
            ConvertFromUom.append(x.find('ConvertFrom').attrib['uom'])
            ConvertToQty.append(x.find('ConvertTo').attrib['qty'])
            ConvertToUom.append(x.find('ConvertTo').attrib['uom'])
    
    
Conversions = pd.DataFrame({'ConversionId': ConversionId, 'Multiplier': Multiplier, 'ConvertFromQty': ConvertFromQty,
                           'ConvertFromUom': ConvertFromUom, 'ConvertToQty': ConvertToQty, 'ConvertToUom': ConvertToUom}
                          ).drop_duplicates()

Conversions.reset_index(drop=True, inplace=True)

In [45]:
# Here we can see for example that to convert 1.14 L to 1 L the multiplier is 0.877 since 1/1.14 = 0.877
Conversions

ConversionId     Multiplier ConvertFromQty ConvertFromUom ConvertToQty  \
0                    1.00000000         1.0000            XXX       1.0000   
1                    0.87719298         1.0000          1.14L       1.1400   
2                    0.66666667         1.0000           1.5L       1.5000   
3                    0.57142857         1.0000         1.75 L       1.7500   
4                    0.50000000         1.0000             2L       2.0000   
5                    0.25000000         1.0000             4L       4.0000   
6                    0.08333333         1.0000           FOOT      12.0000   
7                    0.06250000         1.0000            16L      16.0000   
8                    0.05917160         1.0000         1/2LTR      16.9000   
9                    0.03937008         1.0000          750ML      25.4000   
10                   0.03333333         1.0000        KEG 30L      30.0000   
11                   0.02597403         1.0000         1140ml      38.5000   
12                   0.02500000         1.0000        full in      40.0000   
13                   0.02000000         1.0000        KEG 50L      50.0000   
14                   0.01706485         1.0000        KEG 59L      58.6000   
15                   0.01666667         1.0000           HOUR      60.0000   
16                   0.00200000         1.0000          500ML     500.0000   
17                   0.00153846         1.0000          650ML     650.0000   
18                   0.00151515         1.0000          660ML     660.0000   
19                   0.00142857         1.0000          700ML     700.0000   
20                   0.00140845         1.0000          710ml     710.0000   
21                   0.00133333         1.0000          750ML     750.0000   
22                   0.00059172         1.0000         keg50L    1690.0000   
23                   0.00050403         1.0000         keg59L    1984.0000   
24                   2.00000000         2.0000            cup       1.0000   
25                   2.00000000         2.0000             pt       1.0000   
26                   2.00000000         2.0000           Tbsp       1.0000   
27                   3.00000000         3.0000            tsp       1.0000   
28                   4.00000000         4.0000             qt       1.0000   
29                   8.00000000         8.0000          fl oz       1.0000   
30                  16.00000000        16.0000             oz       1.0000   
31                  28.34950000        28.3495              g       1.0000   
32                  29.57350000        29.5735             ml       1.0000   
33                  35.21126761       100.0000          fl oz       2.8400   
34                1000.00000000      1000.0000              g       1.0000   
35                1000.00000000      1000.0000             mg       1.0000   
36                1000.00000000      1000.0000             ml       1.0000   
37        I-1041     1.00000000         1.0000             CT       1.0000   
38        I-1120     0.02000000         1.0000             CT      50.0000   
39        I-1122     0.01428571         1.0000             CT      70.0000   
40        I-1131     0.00135685         1.0000             CT     737.0000   
41        I-1197     0.01333333         1.0000             CT      75.0000   
42        I-1716    20.00000000        20.0000        BIB 20L       1.0000   
43        I-1758     0.03278689         1.0000          fl oz      30.5000   
44        I-1758     0.00409836         1.0000            cup     244.0000   
45        I-1759     0.03246753         1.0000          fl oz      30.8000   
46        I-1759     0.00413223         1.0000            cup     242.0000   
47        I-1813     0.03278689         1.0000          fl oz      30.5000   
48        I-1813     0.00409836         1.0000            cup     244.0000   
49        I-1814     0.03278689         1.0000          fl oz      30.5000   
50        I-1814     0.004

In [46]:
# Here we can check that there are no ingredients listed since 
Conversions.loc[Conversions["ConversionId"] == "I-4582"]

Empty DataFrame
Columns: [ConversionId, Multiplier, ConvertFromQty, ConvertFromUom, ConvertToQty, ConvertToUom]
Index: []

In [47]:
all_id_list = Items["ItemId"].unique()
all_conv_list = Conversions["ConversionId"].unique()

print("All unique IDs list\n")
print(all_id_list)
print("\n")
print("All unique Conversions list\n")
print(all_conv_list)

All unique IDs list

['I-7631' 'I-2353' 'I-43239' ... 'I-10491' 'I-4962' 'I-4967']


All unique Conversions list

['' 'I-1041' 'I-1120' 'I-1122' 'I-1131' 'I-1197' 'I-1716' 'I-1758'
 'I-1759' 'I-1813' 'I-1814' 'I-1815' 'I-1820' 'I-1821' 'I-1827' 'I-1829'
 'I-2074' 'I-2083' 'I-2115' 'I-2158' 'I-2159' 'I-2188' 'I-2205' 'I-2207'
 'I-2208' 'I-2217' 'I-2220' 'I-2221' 'I-2223' 'I-2236' 'I-2244' 'I-2251'
 'I-2252' 'I-2254' 'I-2306' 'I-2310' 'I-2313' 'I-2489' 'I-2572' 'I-2654'
 'I-2903' 'I-2933' 'I-3141' 'I-3143' 'I-3144' 'I-3145' 'I-3146' 'I-3149'
 'I-3159' 'I-3225' 'I-3229' 'I-3237' 'I-3283' 'I-3284' 'I-3321' 'I-3348'
 'I-3356' 'I-3365' 'I-3367' 'I-3370' 'I-3386' 'I-3387' 'I-3388' 'I-3389'
 'I-3390' 'I-3391' 'I-3392' 'I-3394' 'I-3435' 'I-3449' 'I-3458' 'I-3468'
 'I-3497' 'I-3501' 'I-3517' 'I-3545' 'I-3563' 'I-3572' 'I-3575' 'I-3577'
 'I-3582' 'I-3589' 'I-3590' 'I-3591' 'I-3617' 'I-3619' 'I-3620' 'I-3621'
 'I-3622' 'I-3623' 'I-3624' 'I-3625' 'I-3628' 'I-3629' 'I-3630' 'I-3631'
 'I-3632' 'I-363

In [48]:
# Here we have the number of items in the list that are a part of the "all_id_list" but not part of the "all_conv_list"
missing_conv_id = []

for item in all_id_list:
    if item not in all_conv_list:
        missing_conv_id.append(item)
        
missing_conv_id
print(len(missing_conv_id))

1355


In [49]:
Conversions.shape

(478, 6)

In [50]:
Conversions.loc[Conversions["ConversionId"] == "I-29389"]

Empty DataFrame
Columns: [ConversionId, Multiplier, ConvertFromQty, ConvertFromUom, ConvertToQty, ConvertToUom]
Index: []

In [51]:
Conversions.dtypes

ConversionId      object
Multiplier        object
ConvertFromQty    object
ConvertFromUom    object
ConvertToQty      object
ConvertToUom      object
dtype: object

In [52]:
# Save the dataframe to csv
path = os.path.join(os.getcwd(), "data", "preprocessed", "Conversions_List.csv")
Conversions.to_csv(path, index = False, header = True)

***
## Data Summary

In [53]:
# Summary of raw data imported for evaluation
# Here we have a summary of the number of items, preps, ingredients, products, conversions

datasum = pd.DataFrame([Items.shape, Preps.shape, Ingredients.shape, Products.shape, Conversions.shape],
                       columns = ['count', 'columns'], 
                       index = ['Items', 'Preps', 'Ingredients', 'Products', 'Conversions'])
datasum

count  columns
Items         1618        7
Preps         1514        5
Ingredients  12675        6
Products      1632        3
Conversions    478        6